# Marathon analyse

Het doel is om in dit notebook een analyse te maken van Marathon gegevens.
Het betreft de behaalde tijden van meer dan 37000 lopers van de 42 km Marathon.
De data is vanuit verschillende bronnen verzameld door Prof. Jake Vanderplas

De gegevensset: marathon.csv bevat de volgende gegevens:
- leeftijd
- geslacht M/V  (Man/Vrouw)
- halfweg (tijd na 21 km) (UU:MM:SS)
- finish (tijd na 42 km) (UU:MM:SS)



In [1]:
# importeren van relevante bibliotheken
import numpy as np
import pandas as pd

from bokeh.io import output_notebook, show
from bokeh.layouts import row, gridplot, widgetbox
from bokeh.charts import Histogram, BoxPlot, Scatter, Line, Bar
from bokeh.plotting import figure, ColumnDataSource
from bokeh.models import CustomJS, Slider

output_notebook()

Loading BokehJS ...

### Opdracht A: data mungling

Doel is om de dataset om te vormen naar gegevens die we kunnen analyseren. Dit betekent dat de tijden de nu in uren:minuten en:seconden zijn weergegeven omgevormd moeten worden naar seconden. Een andere belangrijk kenmerk bij marathon lopers is hoe constant er gelopen wordt. Een indicatie hiervoor is het verschil in tijd tussen de eerste 21 km en de tweede 21 km. Dit wordt uitgedrukt in de zogenaande "split_frac" waarde. De formule daarvoor is: 1 - (2 * halfweg in seconden) / (finale in seconden)

1. Lees de gegevensset: marathon.csv in, in een DataFrame
2. laat zien welke gegevens (.head()) erin zitten met bebehorende type (.dtypes)
3. vorm halfweg en finish kolommen om naar de tijd in seconden:
     * splits kolommen kan met: h,m,s = map(int. s.split(':')  (s=kolom)
     * bereken de seconden: h * 3600 + m * 60 + s
4. Voeg een kolom split_frac toe 

Laat zien dat de dataset nu de volgende kolommen bevat: leeftijd, geslacht, halfweg, halfwegsec, finish, finishsec, split_frac



In [2]:
df = pd.read_csv('marathon.csv')

In [3]:
df.head()

leeftijd geslacht   halfweg    finish
0        33        M  01:05:38  02:08:51
1        32        M  01:06:26  02:09:28
2        31        M  01:06:49  02:10:42
3        38        M  01:06:16  02:13:45
4        31        M  01:06:32  02:13:59

In [4]:
df.dtypes

leeftijd     int64
geslacht    object
halfweg     object
finish      object
dtype: object

In [5]:
hwsec = []
for t in df.halfweg.str.split(':'):
    sec = (int(t[0])*3600) + (int(t[1])*60) + int(t[2])
    hwsec.append(sec)
    
fnsec = []
for t in df.finish.str.split(':'):
    sec = (int(t[0])*3600) + (int(t[1])*60) + int(t[2])
    fnsec.append(sec)
    
df["halfwegsec"] = hwsec
df["finishsec"] = fnsec

In [10]:
df["split_frac"] = df.finishsec - df.halfwegsec*2
df

leeftijd geslacht   halfweg    finish  halfwegsec  finishsec  \
0            33        M  01:05:38  02:08:51        3938       7731   
1            32        M  01:06:26  02:09:28        3986       7768   
2            31        M  01:06:49  02:10:42        4009       7842   
3            38        M  01:06:16  02:13:45        3976       8025   
4            31        M  01:06:32  02:13:59        3992       8039   
5            31        M  01:06:13  02:14:11        3973       8051   
6            27        M  01:06:40  02:14:28        4000       8068   
7            31        M  01:06:31  02:15:16        3991       8116   
8            30        M  01:05:39  02:15:57        3939       8157   
9            30        M  01:05:40  02:16:39        3940       8199   
10           26        M  01:08:10  02:18:18        4090       8298   
11           29        M  01:05:54  02:18:52        3954       8332   
12           28        M  01:08:59  02:19:36        4139       8376   
13           24        M  01:09:16  02:19:45        4156       8385   
14           37        M  01:05:21  02:19:47        3921       8387   
15           25        M  01:09:52  02:20:17        4192       8417   
16           22        M  01:09:53  02:20:57        4193       8457   
17           30        M  01:05:40  02:21:17        3940       8477   
18           26        M  01:10:11  02:21:24        4211       8484   
19           36        M  01:10:35  02:21:55        4235       8515   
20           28        M  01:11:59  02:22:14        4319       8534   
21           31        M  01:05:54  02:22:20        3954       8540   
22           41        M  01:09:14  02:22:27        4154       8547   
23           24        M  01:11:18  02:22:55        4278       8575   
24           26        M  01:10:17  02:22:56        4217       8576   
25           36        M  01:06:39  02:23:31        3999       8611   
26           28        M  01:10:32  02:23:39        4232       8619   
27           29        M  01:12:25  02:23:48        4345       8628   
28           34        V  01:12:35  02:24:13        4355       8653   
29           31        M  01:14:07  02:25:19        4447       8719   
...         ...      ...       ...       ...         ...        ...   
37220        52        M  03:20:00  08:46:04       12000      31564   
37221        53        M  03:40:34  08:46:39       13234      31599   
37222        60        M  03:39:16  08:46:48       13156      31608   
37223        57        M  03:47:08  08:46:58       13628      31618   
37224        61        M  03:32:20  08:47:25       12740      31645   
37225        41        M  03:43:25  08:49:12       13405      31752   
37226        24        M  03:34:01  08:49:36       12841      31776   
37227        79        M  03:28:31  08:49:46       12511      31786   
37228        24        V  03:35:21  08:50:47       12921      31847   
37229        60        V  03:49:33  08:50:58       13773      31858   
37230        50        V  03:43:48  08:52:14       13428      31934   
37231        35        V  02:53:57  08:54:12       10437      32052   
37232        43        V  03:41:15  08:57:29       13275      32249   
37233        27        V  03:37:49  08:57:41       13069      32261   
37234        47        V  03:38:05  08:57:45       13085      32265   
37235        37        V  03:48:55  08:58:03       13735      32283   
37236        55        M  03:48:44  08:58:38       13724      32318   
37237        59        V  03:40:39  08:58:39       13239      32319   
37238        71        M  03:48:30  09:00:00       13710      32400   
37239        68        V  03:49:51  09:00:48       13791      32448   
37240        73        M  03:46:01  09:01:31       13561      32491   
37241        42        V  03:27:53  09:05:44       12473      32744   
37242        64        V  04:27:19  09:10:58       16039      33058   
37243        67        M  04:19:47  09:16:15       15587      33375   
37244        32        V  04:15

### Opdracht B: data exploration
Doel is om inzicht te krijgen in de te analyseren gegegevens. N.B. we maken gebruik van Bokeh om de diagrammen te tonen. Maak hierbij zo veel mogelijk gebruik van high-level API van Bokeh.

1. Laat met 3 histogrammen op 1 rij zien hoe de halfwegtijden (in seconden), finishtijden (in seconden) en split_frac gegevens zijn verdeeld. 
    * wat kun je zeggen over de mate van normale verdeling ?
2. Laat met een histogram zien hoe de finishtijden (in seconden) tussen mannen en vrouwen zijn verdeeld. 
    * wat concludeer je daaruit ?
3. Laat met een Boxplot zien hoe de leeftijd verdeling per geslacht (M/V) is
    * wat zijn de bijbehorende waarden voor 25%, 50%, 75% en interkwartielafstand ?
4. Laat met een Scatterplot zien hoe de relatie ligt tussen de halfweg- en finishtijden (in seconden). Laat in de kleur uitkomen wat het geslacht is.
    * wat concludeer je hier uit ?



In [25]:
show(row([Histogram(df.halfwegsec), Histogram(df.finishsec), Histogram(df.split_frac)]))

In [73]:
# Get separated series
# m = df.loc[df.geslacht == 'M']
# v = df.loc[df.geslacht == 'V']
show(Histogram(df, values='finishsec', label='geslacht', color='geslacht'))

In [74]:
show(BoxPlot(df, values='leeftijd', label='geslacht', color='geslacht'))

In [35]:
show(Scatter(df, x='halfwegsec', y='finishsec', color='geslacht'))

### Opdracht C correlatie analyse
Zoals hierboven uitgelegd is de "split_frac" een maat voor hoe constant de loopsnelheid is geweest bij het lopen van de marathon. We gaan nu een onderzoek doen van de correlatie van Spilt_frac en de andere variabelen: leeftijd, halfwegtijd in seconden en finishtijd in seconden.

1. Laat met scatterplots in een grid zien hoe de correlatie is tussen de variabelen split_frac, leeftijd, halfwegtijd in seconden en finishtijd in seconden
    * wat concludeer je uit de diagrammen ?
2. Zoek op internet naar de mogelijheden van Seaborn voor wat betreft PairGrids. Wat haal je daaruit ?
    * Kun je zoiets ook voor Bokeh vinden ? 


In [36]:
show(row([Scatter(df, x='split_frac', y='leeftijd'),
          Scatter(df, x='split_frac', y='halfwegsec'),
          Scatter(df, x='split_frac', y='finishsec')]))

### Opdracht D leeftijdsonderzoek
Het is interessant om een onderzoek te doen naar de finishtijden voor de verschillende leeftijden en voor de 
verschillen tussen mannen en vrouwen.

Hiervoor willen we een interactieve oplossing hebben, met daarbij minimaal de volgende mogelijkheden:
- Basis is een diagram met op de X-as de leeftijden en op de Y-as de finishtijden
- Selectie op leeftijdgroep (suggestie: sliders voor minimumleeftijd en maximumleeftijd)

Doe dit in de volgende stappen:
1. Vorm de gegevensset om naar een gegevensset met de volgende inhoud: leeftijd, finishman, finischvrouw, finishbeide
    * aanwijzing: gebruik groupby en merge
2. Teken een figuur met daarin de drie lijnen van finishtijden per leeftijd. De leeftijd is de X-as.
3. Probeer nu interactiviteit toe te voegen met behulp van sliders
    * Dit is een hele uitdagende klus, begin heel eenvoudig met 1 grafiek en 1 slider

In [72]:
src = ColumnDataSource(data=dict(x=df.leeftijd, y=df.finishsec))

f = figure()
f.line('x', 'y', source=src)

cb = CustomJS(args=dict(source=src), code="""
    var data = data.source,
        age = age.value,
        x = data['x'],
        y = data['y'];
        console.log(data); // undefined
    for (i = 0; i < x.length; i++) {
        if (x[i] == age) {
            x[i].visible = true;
            y[i].visible = true;
        } else {
            x[i].visible = false;
            y[i].visible = false;
        }
    }
    source.trigger('change');
""")

age = Slider(title="Leeftijd", start=df.leeftijd.min(), end=df.leeftijd.max(), step=1, value=df.leeftijd.min(), callback=cb)

cb.args['age'] = age

layout = row(f, widgetbox(age))

show(layout)